In [8]:
import numpy as np
import pandas as pd
import os
from sklearn.metrics import classification_report, confusion_matrix
import logging
import torch
import chart_studio.plotly as py
import plotly.graph_objs as go
from plotly.offline import iplot, init_notebook_mode
# Using plotly + cufflinks in offline mode
import cufflinks
cufflinks.go_offline(connected=True)
init_notebook_mode(connected=True)

In [9]:
def contact_detection_accuracy(df, allowable_delay = 20):
    "df should include label, majority voting and time"
    TP, TN, FP, FN = 0, 0, 0, 0
    
    df['label_diff'] = df['label'].diff().fillna(0)
    df['TP'], df['TN'], df['FP'], df['FN'] = None, None, None, None
 
    contact_delays = []
    no_contact_delays = []
    df = df.reset_index(drop=True)
 
    change_events = df[df['label_diff'] != 0].index.tolist()
 
    # Add first and last index if not present
    if 0 not in change_events:
        change_events.insert(0, 0)
    if len(df) - 1 not in change_events:
        change_events.append(len(df) - 1)
 
    for event_idx in range(len(change_events) - 1):
        idx = change_events[event_idx]
        
        if df.label[idx] == 1: # Starting a contact event
            for i in range(idx, min(idx + allowable_delay, len(df))):
                if df.majority_voting[i] == 1:
                    delay = df.time[i] - df.time[idx]
                    contact_delays.append(delay)
                    break
            
            if i >= (idx + allowable_delay - 1):
                contact_delays.append(0)
 
            # Calculate TP and FN
            for j in range(change_events[event_idx+1], max(change_events[event_idx+1]-allowable_delay, 0), -1):
                if df.majority_voting[j] == 1:
                    break
 
            for idx_ in range(i, j):
                if df.majority_voting[idx_] == df.label[idx_]:
                    TP += 1
                    df.loc[idx_, 'TP'] = 0.9
                else:
                    FN += 1
                    df.loc[idx_, 'FN'] = 0.9
 
        else: # Starting a contact-free event
 
            for i in range(idx, min(idx + allowable_delay, len(df))):
                if df.majority_voting[i] == 0:
                    delay = df.time[i] - df.time[idx]
                    no_contact_delays.append(delay)
                    break
            
            if i >= (idx + allowable_delay - 1):
                no_contact_delays.append(0)
 
            # Calculate TN and FP
            for j in range(change_events[event_idx+1], max(change_events[event_idx+1]-allowable_delay, 0), -1):
                if df.majority_voting[j] == 0:
                    break
                
            for idx_ in range(i, j):
                if df.majority_voting[idx_] == df.label[idx_]:
                    TN += 1
                    df.loc[idx_, 'TN'] = 0.1
                else:
                    FP += 1
                    df.loc[idx_, 'FP'] = 0.1
 
    # Compute averages safely
    contact_avg_delay = np.nanmean([d for d in contact_delays if d > 0])
    no_contact_avg_delay = np.nanmean([d for d in no_contact_delays if d > 0])
 
    ModelAccuracy = (TP + TN) / (TP + TN + FP + FN) * 100
    DetectionFailureRate = FN / (TP + FN) * 100
    FalseAlarmRate = FP / (TN + FP) * 100
 
    return df, TP, TN, FP, FN, contact_avg_delay, no_contact_avg_delay, ModelAccuracy, DetectionFailureRate, FalseAlarmRate, contact_delays, no_contact_delays
 

In [11]:
# 批处理
data_path = '../DATA/'
dataset_path  = os.path.join(data_path, 'Labeled_data/ModelLabeled')
output_file = os.path.join(data_path, 'model_performance_resultspose123_1.csv')


valid_models = { "GRU","LSTM","NCPCfC","RT2DCNN", "STFT2DCNN", "STT2DCNN", "RT3DCNN", "STFT3DCNN","STT3DCNN"}

files_and_dirs = os.listdir(dataset_path )
valid_folders = [f for f in files_and_dirs if len(f.split("_")) > 1 and f.split("_")[1] in valid_models]

# print(f"Valid folders: {valid_folders}")
results = []


for folder_name in valid_folders:
    # print(f"Processing folder: {folder_name}")
    data_file_path = os.path.join(dataset_path, folder_name, 'labeled_modelResult_data.csv')
    
    if not os.path.exists(data_file_path):
        print(f"Skipping {folder_name}, labeled_modelResult_data.csv not found.")
        continue
    
    df = pd.read_csv(data_file_path)
    df, TP, TN, FP, FN, contact_avg_delay, no_contact_avg_delay, ModelAccuracy, DetectionFailureRate, FalseAlarmRate, contact_delays, no_contact_delays = contact_detection_accuracy(df, 20)
    
    model_name = folder_name.split("_")[1]  # 提取模型名称
    
    results.append({
        "folder_name": folder_name,
        "model_name": model_name,
        "Accuracy": ModelAccuracy,
        "DetectionFailureRate": DetectionFailureRate,
        "FalseAlarmRate": FalseAlarmRate,
        "ContactDetectionDelay_ms": contact_avg_delay * 1000,
        "NoContactDetectionDelay_ms": no_contact_avg_delay * 1000,
        "TP": TP,
        "TN": TN,
        "FP": FP,
        "FN": FN
    })
    

    
    print(f"Model: {folder_name}, Accuracy: {ModelAccuracy:.2f}%, DetectionFailureRate: {DetectionFailureRate:.2f}%, FalseAlarmRate: {FalseAlarmRate:.2f}%, Contact Detection Delay: {contact_avg_delay*1000:.3f}ms, No-Contact Detection Delay: {no_contact_avg_delay*1000:.3f}ms, TP: {TP}, TN: {TN}, FP: {FP}, FN: {FN}")

    # 保存结果到CSV文件
results_df = pd.DataFrame(results)
results_df.to_csv(output_file, index=False)

print(f"Results saved to {output_file}")

/tmp/ipykernel_4819/3782058487.py:72: RuntimeWarning:

Mean of empty slice



Model: 0305_RT3DCNN_Post123_T4ES_P, Accuracy: 95.94%, DetectionFailureRate: 0.00%, FalseAlarmRate: 6.31%, Contact Detection Delay: 62.501ms, No-Contact Detection Delay: nanms, TP: 2031, TN: 3427, FP: 231, FN: 0
Model: 0305_STT3DCNN_Post123_T4ES4+7_G, Accuracy: 97.68%, DetectionFailureRate: 2.84%, FalseAlarmRate: 2.03%, Contact Detection Delay: 45.004ms, No-Contact Detection Delay: 84.999ms, TP: 2186, TN: 3997, FP: 83, FN: 64


/tmp/ipykernel_4819/3782058487.py:72: RuntimeWarning:

Mean of empty slice



Model: 0305_STFT3DCNN_Post123_T4ESBN7+1_ST, Accuracy: 94.47%, DetectionFailureRate: 0.00%, FalseAlarmRate: 5.62%, Contact Detection Delay: 60.001ms, No-Contact Detection Delay: nanms, TP: 79, TN: 4296, FP: 256, FN: 0


/tmp/ipykernel_4819/3782058487.py:72: RuntimeWarning:

Mean of empty slice



...

Model: 0220_RT2DCNN_Post123_T4ES_P, Accuracy: 94.99%, DetectionFailureRate: 0.00%, FalseAlarmRate: 8.81%, Contact Detection Delay: 64.998ms, No-Contact Detection Delay: nanms, TP: 1709, TN: 2049, FP: 198, FN: 0
Model: 0305_STFT3DCNN_Post123_T4ESBN7+1_G, Accuracy: 97.78%, DetectionFailureRate: 4.17%, FalseAlarmRate: 1.40%, Contact Detection Delay: 41.005ms, No-Contact Detection Delay: 56.669ms, TP: 1928, TN: 4728, FP: 67, FN: 84
Model: 0220_GRU_Post123_T4ES_ST, Accuracy: 94.63%, DetectionFailureRate: 0.00%, FalseAlarmRate: 5.53%, Contact Detection Delay: 29.009ms, No-Contact Detection Delay: 85.013ms, TP: 103, TN: 3141, FP: 184, FN: 0


/tmp/ipykernel_4819/3782058487.py:72: RuntimeWarning:

Mean of empty slice



Model: 0305_STFT3DCNN_Post123_T4ESBN7+1_P, Accuracy: 96.41%, DetectionFailureRate: 0.74%, FalseAlarmRate: 5.44%, Contact Detection Delay: 53.331ms, No-Contact Detection Delay: nanms, TP: 2019, TN: 2973, FP: 171, FN: 15


/tmp/ipykernel_4819/3782058487.py:72: RuntimeWarning:

Mean of empty slice



Model: 0305_STT3DCNN_Post123_T4ES4+7_ST, Accuracy: 93.12%, DetectionFailureRate: 0.00%, FalseAlarmRate: 6.99%, Contact Detection Delay: 55.001ms, No-Contact Detection Delay: nanms, TP: 72, TN: 3989, FP: 300, FN: 0
Model: 0220_NCPCfC_Post123_T4ES_G, Accuracy: 94.68%, DetectionFailureRate: 3.08%, FalseAlarmRate: 6.69%, Contact Detection Delay: 56.670ms, No-Contact Detection Delay: 52.496ms, TP: 2140, TN: 3363, FP: 241, FN: 68
Results saved to ../DATA/model_performance_resultspose123_1.csv


In [49]:
# 单个文件夹处理
df = pd.read_csv('../DATA/Labeled_data/ModelDATA/0305_STFT3DCNN_Post123_T4ES_P/labeled_modelResult_data.csv')
# Call the function
df, TP, TN, FP, FN, contact_avg_delay, no_contact_avg_delay, ModelAccuracy, DetectionFailureRate, FalseAlarmRate, contact_delays, no_contact_delays = contact_detection_accuracy(df, 20)
 
print('contact_delays:', contact_delays)
print('no_contact_delays:', no_contact_delays)
print(f"Accuracy:{ModelAccuracy:.2f}%, DetectionFailureRate:{DetectionFailureRate:.2f}%, FalseAlarmRate:{FalseAlarmRate:.2f}%, Contact Detection Delay: {contact_avg_delay*1000:.3f}ms, No-Contact Detection Delay: {no_contact_avg_delay*1000:.3f}ms, TP: {TP}, TN: {TN}, FP: {FP}, FN: {FN}")
 
# Plot results
df[['time', 'label', 'majority_voting', 'TP', 'TN', 'FP', 'FN']].iplot(
    x='time', kind='scatter',
    mode={'label': 'lines', 'majority_voting': 'lines', 'TP': 'markers', 'TN': 'markers', 'FP': 'markers', 'FN': 'markers'},
    title='Contact Detection Analysis (Interactive)',
    xTitle='Time Index', yTitle='Signal', theme='white',
    symbol=[None, None, 'x', 'x', 'x', 'x'],
    size = 5,
    colors=['blue', 'pink', 'green', 'lightgreen', 'orange', 'red'],
)


df

contact_delays: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
no_contact_delays: [0.0, 0, 0, 0, 0, 0, 0, 0, 0.0, 0.0, 0.0]
Accuracy:52.81%, DetectionFailureRate:67.69%, FalseAlarmRate:38.89%, Contact Detection Delay: nanms, No-Contact Detection Delay: nanms, TP: 486, TN: 2269, FP: 1444, FN: 1018


/tmp/ipykernel_2521670/3782058487.py:71: RuntimeWarning:

Mean of empty slice

/tmp/ipykernel_2521670/3782058487.py:72: RuntimeWarning:

Mean of empty slice



index       time    tau_J0     tau_J1    tau_J2     tau_J3    tau_J4  \
0         1   0.000000 -0.037866 -36.200062  0.536611  16.276621  0.327171   
1         2   0.004997 -0.002160 -36.124683  0.536611  16.236948  0.336326   
2         3   0.009996 -0.002160 -36.124683  0.536611  16.236948  0.336326   
3         4   0.015004 -0.002160 -36.164356  0.608022  16.312326  0.327171   
4         5   0.020004 -0.002160 -36.164356  0.608022  16.312326  0.327171   
...     ...        ...       ...        ...       ...        ...       ...   
5593   5594  27.964994 -0.264001 -36.200062  0.496938  16.312326  0.318015   
5594   5595  27.970004 -0.264001 -36.200062  0.496938  16.312326  0.318015   
5595   5596  27.975000 -0.264001 -36.200062  0.496938  16.387705  0.308860   
5596   5597  27.979991 -0.264001 -36.200062  0.496938  16.387705  0.308860   
5597   5598  27.984988 -0.264001 -36.200062  0.461232  16.312326  0.299705   

        tau_J5    tau_J6  tau_J_d0  ...   etau_J6  label  model_result_time  \
0     2.289623 -0.028515       0.0  ...  0.028515      0           0.000000   
1     2.279552 -0.028515       0.0  ...  0.028515      0           0.007003   
2     2.279552 -0.028515       0.0  ...  0.028515      0           0.012384   
3     2.289623 -0.018444       0.0  ...  0.018444      0           0.012384   
4     2.289623 -0.018444       0.0  ...  0.018444      0           0.017746   
...        ...       ...       ...  ...       ...    ...                ...   
5593  2.289623 -0.099926       0.0  ...  0.099926      0          27.966748   
5594  2.289623 -0.099926       0.0  ...  0.099926      0          27.972808   
5595  2.310680 -0.038585       0.0  ...  0.038585      0          27.972808   
5596  2.310680 -0.038585       0.0  ...  0.038585      0          27.979036   
5597  2.299694 -0.059643       0.0  ...  0.059643      0          27.983698   

      touch_type_idx  majority_voting  label_diff    TP    TN    FP    FN  
0                0.0                0         0.0  None   0.1  None  None  
1                0.0                0         0.0  None   0.1  None  None  
2                0.0                0         0.0  None   0.1  None  None  
3                0.0                0         0.0  None   0.1  None  None  
4                0.0                0         0.0  None   0.1  None  None  
...              ...              ...         ...   ...   ...   ...   ...  
5593             0.0                0         0.0  None   0.1  None  None  
5594             0.0                0         0.0  None   0.1  None  None  
5595             0.0                0         0.0  None   0.1  None  None  
5596             0.0                0         0.0  None   0.1  None  None  
5597             0.0                0         0.0  None  None  None  None  

[5598 rows x 81 columns]

In [13]:
# 单个文件夹处理-带IDX
df = pd.read_csv('../DATA/Labeled_data/ModelDATA/0220_1L3DTCNN_Post123_T4ES_G/labeled_modelResult_data.csv')
# Call the function
df, TP, TN, FP, FN, contact_avg_delay, no_contact_avg_delay, ModelAccuracy, DetectionFailureRate, FalseAlarmRate, contact_delays, no_contact_delays = contact_detection_accuracy(df, 20)
 
print('contact_delays:', contact_delays)
print('no_contact_delays:', no_contact_delays)
print(f"Accuracy:{ModelAccuracy:.2f}%, DetectionFailureRate:{DetectionFailureRate:.2f}%, FalseAlarmRate:{FalseAlarmRate:.2f}%, Contact Detection Delay: {contact_avg_delay*1000:.3f}ms, No-Contact Detection Delay: {no_contact_avg_delay*1000:.3f}ms, TP: {TP}, TN: {TN}, FP: {FP}, FN: {FN}")
 
# Plot results
df[['time', 'label', 'majority_voting', 'touch_type_idx', 'TP', 'TN', 'FP', 'FN']].iplot(
    x='time', kind='scatter',
    mode={'label': 'lines', 'majority_voting': 'lines', 'touch_type_idx': 'lines', 'TP': 'markers', 'TN': 'markers', 'FP': 'markers', 'FN': 'markers'},
    title='Contact Detection Analysis (Interactive)',
    xTitle='Time Index', yTitle='Signal', theme='white',
    symbol=[None, None, None, 'x', 'x', 'x', 'x'],
    size = 5,
    colors=['blue', 'pink', 'green', 'lightgreen', 'orange', 'red'],
)


df

contact_delays: [0, 0.014997831982327625, 0, 0, 0.05500609902082765, 0, 0.04994306698790396, 0.0, 0.09500871298951097, 0, 0]
no_contact_delays: [0.0, 0, 0, 0, 0.07500624799286015, 0, 0, 0, 0, 0, 0.07499232501140796]
Accuracy:97.22%, DetectionFailureRate:5.87%, FalseAlarmRate:1.16%, Contact Detection Delay: 53.739ms, No-Contact Detection Delay: 74.999ms, TP: 2052, TN: 4107, FP: 48, FN: 128


index       time    tau_J0     tau_J1    tau_J2     tau_J3    tau_J4  \
0         1   0.000000 -0.224328 -36.049305  0.536611  16.276621  0.318015   
1         2   0.005004 -0.224328 -36.049305  0.536611  16.276621  0.318015   
2         3   0.009990 -0.188623 -36.085011  0.496938  16.312326  0.327171   
3         4   0.014998 -0.188623 -36.085011  0.496938  16.312326  0.327171   
4         5   0.019995 -0.188623 -36.085011  0.572316  16.236948  0.318015   
...     ...        ...       ...        ...       ...        ...       ...   
6656   6657  33.280002 -0.224328 -36.009632  0.536611  16.276621  0.308860   
6657   6658  33.284993 -0.264001 -36.085011  0.572316  16.276621  0.299705   
6658   6659  33.290008 -0.264001 -36.085011  0.572316  16.276621  0.299705   
6659   6660  33.295022 -0.188623 -36.009632  0.536611  16.276621  0.308860   
6660   6661  33.300002 -0.188623 -36.009632  0.536611  16.276621  0.308860   

        tau_J5    tau_J6  tau_J_d0  ...   etau_J6  label  model_result_time  \
0     2.299694 -0.049572       0.0  ...  0.049572      0           0.000000   
1     2.299694 -0.049572       0.0  ...  0.049572      0           0.000000   
2     2.299694 -0.049572       0.0  ...  0.049572      0           0.000000   
3     2.299694 -0.049572       0.0  ...  0.049572      0           0.023558   
4     2.289623 -0.038585       0.0  ...  0.038585      0           0.023558   
...        ...       ...       ...  ...       ...    ...                ...   
6656  2.279552 -0.059643       0.0  ...  0.059643      0          33.279766   
6657  2.279552  0.031910       0.0  ... -0.031910      0          33.286372   
6658  2.279552  0.031910       0.0  ... -0.031910      0          33.289486   
6659  2.279552 -0.049572       0.0  ...  0.049572      0          33.294984   
6660  2.279552 -0.049572       0.0  ...  0.049572      0          33.299994   

      touch_type_idx  majority_voting  label_diff    TP    TN    FP    FN  
0                0.0                0         0.0  None   0.1  None  None  
1                0.0                0         0.0  None   0.1  None  None  
2                0.0                0         0.0  None   0.1  None  None  
3                0.0                0         0.0  None   0.1  None  None  
4                0.0                0         0.0  None   0.1  None  None  
...              ...              ...         ...   ...   ...   ...   ...  
6656             0.0                0         0.0  None   0.1  None  None  
6657             0.0                0         0.0  None   0.1  None  None  
6658             0.0                0         0.0  None   0.1  None  None  
6659             0.0                0         0.0  None   0.1  None  None  
6660             0.0                0         0.0  None  None  None  None  

[6661 rows x 81 columns]

In [12]:
# 批处理

data_path = '../DATA/'
dataset_path = os.path.join(data_path, 'Labeled_data/ModelLabeled')
output_file = os.path.join(data_path, 'model_performance_resultspose123_2.csv')

gesture_mapping = {"NC": 0, "ST": 1, "P": 2, "G": 3}
valid_models = { "GRU","LSTM","NCPCfC","RT2DCNN", "STFT2DCNN", "STT2DCNN", "RT3DCNN", "STFT3DCNN","STT3DCNN"}

files_and_dirs = os.listdir(dataset_path)
valid_folders = [f for f in files_and_dirs if len(f.split("_")) > 1 and f.split("_")[1] in valid_models]

print(f"Valid folders: {valid_folders}")

results = []

for folder_name in valid_folders:
    print(f"Processing folder: {folder_name}")
    folder_path = os.path.join(dataset_path, folder_name)
    # save_data_file = os.path.join(dataset_path, folder_name)
    csv_file = os.path.join(folder_path, 'labeled_modelResult_data.csv')
    
    if not os.path.exists(csv_file):
        print(f"Skipping {folder_name}: labeled_modelResult_data.csv not found")
        continue
    
    df = pd.read_csv(csv_file)
    y_true = []
    y_pred = []
    
    touch_type_from_folder = folder_name.split('_')[-1]
    model_name = folder_name.split('_')[1]  # 提取模型名称
    
    for index, row in df.iterrows():
        if (row['label'] == 1) & (row['majority_voting'] == 1):
            y_true.append(gesture_mapping.get(touch_type_from_folder, 0))
            y_pred.append(row['touch_type_idx'])
    
    if y_true and y_pred:
        conf_matrix = confusion_matrix(y_true, y_pred, labels=list(gesture_mapping.values()))
        total_samples = conf_matrix.sum()
        true_positives = conf_matrix.diagonal().sum()
        accuracy = (true_positives / total_samples) * 100 if total_samples > 0 else 0
        failure_rate = [
            ((conf_matrix[i].sum() - conf_matrix[i, i]) / conf_matrix[i].sum()) * 100
            if conf_matrix[i].sum() > 0 else 0
            for i in range(len(conf_matrix))
        ]
        print(f"Folder: {folder_name}")
        print(f"Model: {model_name}")
        print(f"Accuracy: {accuracy:.2f}%")
        print(f"Detection Failure Rate (by class): {failure_rate}")
        print("Confusion Matrix:\n", conf_matrix)

        results.append([folder_name, model_name, accuracy, failure_rate])
    else:
        print(f"Skipping {folder_name}: No valid data for y_true and y_pred")

results_df = pd.DataFrame(results, columns=["folder_name", "model_name", "accuracy", "failure_rate"])
results_df.to_csv(output_file, index=False)
print("Results saved to model_results.csv")


Valid folders: ['0305_RT3DCNN_Post123_T4ES_P', '0305_STT3DCNN_Post123_T4ES4+7_G', '0305_STFT3DCNN_Post123_T4ESBN7+1_ST', '0220_GRU_Post123_T4ES_G', '0220_STT2DCNN_Post123_T4ES_ST', '0220_STT2DCNN_Post123_T4ES_P', '0220_STFT2DCNN_Post123_T4ES_P', '0220_NCPCfC_Post123_T4ES_ST', '0220_LSTM_Post123_T4ES_ST', '0220_LSTM_Post123_T4ES_P', '0220_RT2DCNN_Post123_T4ES_ST', '0220_STFT2DCNN_Post123_T4ES_G', '0220_LSTM_Post123_T4ES_G', '0305_RT3DCNN_Post123_T4ES_ST', '0220_NCPCfC_Post123_T4ES_P', '0220_RT2DCNN_Post123_T4ES_G', '0220_STFT2DCNN_Post123_T4ES_ST', '0220_GRU_Post123_T4ES_P', '0305_RT3DCNN_Post123_T4ES_G', '0220_STT2DCNN_Post123_T4ES1_G', '0305_STT3DCNN_Post123_T4ES4+7_P', '0220_RT2DCNN_Post123_T4ES_P', '0305_STFT3DCNN_Post123_T4ESBN7+1_G', '0220_GRU_Post123_T4ES_ST', '0305_STFT3DCNN_Post123_T4ESBN7+1_P', '0305_STT3DCNN_Post123_T4ES4+7_ST', '0220_NCPCfC_Post123_T4ES_G']
Processing folder: 0305_RT3DCNN_Post123_T4ES_P
Folder: 0305_RT3DCNN_Post123_T4ES_P
Model: RT3DCNN
Accuracy: 95.77%
Dete

In [4]:
# 单文件处理
import os
import pandas as pd

gesture_mapping = {"NC": 0, "ST": 1, "P": 2, "G": 3}

# Assuming your data is loaded into a pandas DataFrame from 'labeled_modelResult_data.csv'
df = pd.read_csv('../DATA/Labeled_data/0213_2LCNN_Post1_ST/labeled_modelResult_data.csv')

# Initialize lists for y_true and y_pred
y_true = []
y_pred = []

# Extract touch type from folder name dynamically
folder_path = '../DATA/Labeled_data/0213_2LCNN_Post1_ST'  
folder_name = os.path.basename(folder_path)  # Get the folder name (e.g., '0213_2LCNN_Post1_ST')
touch_type_from_folder = folder_name.split('_')[-1]  

# Loop through each row in the DataFrame to apply the logic
for index, row in df.iterrows():
    # Determine y_true
    if (row['label'] == 1) & (row['majority_voting'] == 1):
        # If there is a touch (label=1), extract touch type from folder name
        y_true.append(gesture_mapping[touch_type_from_folder])
    # else:
    #     # If there is no touch (label=0), set y_true as NC
    #     y_true.append(gesture_mapping["NC"])

    # Determine y_pred based on majority voting
    if  (row['label'] == 1) & (row['majority_voting'] == 1):
        # If majority_voting=1, set y_pred to touch_type_idx
        y_pred.append(row['touch_type_idx'])
    # else:
    #     # If majority_voting=0, set y_pred as NC (0)
    #     y_pred.append(gesture_mapping["NC"])

# 计算混淆矩阵
conf_matrix = confusion_matrix(y_true, y_pred, labels=list(gesture_mapping.values()))

# 计算准确率
total_samples = conf_matrix.sum()
true_positives = conf_matrix.diagonal().sum()
accuracy = (true_positives / total_samples) * 100 if total_samples > 0 else 0

# 计算检测失败率
failure_rate = [
    ((conf_matrix[i].sum() - conf_matrix[i, i]) / conf_matrix[i].sum()) * 100
    if conf_matrix[i].sum() > 0 else 0
    for i in range(len(conf_matrix))
]

print(f"Accuracy: {accuracy:.2f}%")
print(f"Detection Failure Rate (by class): {failure_rate}")
print("Confusion Matrix:\n", conf_matrix)


Accuracy: 88.24%
Detection Failure Rate (by class): [0, 11.76470588235294, 0, 0]
Confusion Matrix:
 [[ 0  0  0  0]
 [ 0 15  2  0]
 [ 0  0  0  0]
 [ 0  0  0  0]]


In [13]:
from IPython.core.display import display, HTML
result = pd.read_csv("../DATA/model_performance_resultspose123_1.csv")
display(HTML(result.to_html(max_rows=100))) 
model_performance_summary = result.groupby('model_name')[["Accuracy","DetectionFailureRate","FalseAlarmRate","ContactDetectionDelay_ms","NoContactDetectionDelay_ms"]].mean()
display(HTML(model_performance_summary.to_html(max_rows=100))) 


/tmp/ipykernel_4819/495763260.py:1: DeprecationWarning:

Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display



In [14]:
from IPython.core.display import display, HTML
result2 = pd.read_csv("../DATA/model_performance_resultspose123_2.csv")
result2 = result2.sort_values(by="model_name")
display(HTML(result2.to_html(max_rows=100))) 
model_performance_summary = result2.groupby('model_name')[["accuracy"]].mean()
display(HTML(model_performance_summary.to_html(max_rows=100))) 

/tmp/ipykernel_4819/2749139411.py:1: DeprecationWarning:

Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display



In [ ]:
#不运行， 这是原代码
data_name, dof, batch_size = 'franka_main', 7 , 62
 
 
best_models_index, folder_name , data_name, dof  = ([   [1, 64, 3, 50],
                                                        [1, 64, 3, 80],
                                                        [1, 64, 3, 100],
                                                        [1, 64, 5, 50],
                                                        [1, 64, 5, 80],
                                                        [1, 64, 5, 100],
                                                        [1, 128, 3, 50],
                                                        [1, 128, 3, 80],
                                                        [1, 128, 3, 100],
                                                        [1, 128, 5, 50],
                                                        [1, 128, 5, 80],
                                                        [1, 128, 5, 100] ], f'{data_name}/trained_models/contact_localization/{batch_size}/', f'{data_name}', dof)
 
logging.info(f'trained model on {folder_name}, tested on {data_name}, with {dof} links')
 
#best_models_index = [[1, 128, 3, 80]]
# hyperparameters
 
n = 14  # Window size for majority voting
 
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
 
if device.type == "cuda":
    print("Using GPU:", torch.cuda.get_device_name())
 
main_path = os.getcwd().replace('AIModels', '')
 
 
dict_label = {'link7': 7, 'link6':6, 'link5':5, 'link4':4, 'link3':3, 'link2':2, 'link1':1, 'no_contact': 0}
selected_features = [f'e{i}' for i in range(dof)]#+[ f'de{i}' for i in range(robot_dof)]
 
# Load dataset ONCE outside the model loop
testing_datasets = LoadDatasets(os.getcwd().replace('AIModels', '') + f'/dataset/{data_name}/labeled_data/', dict_label)
test_datasetloader = DataLoader(testing_datasets, batch_size=1, shuffle=False)
 
file_predictions = {}
for link in dict_label.keys():
    for trial_dataset_path, label in test_datasetloader:
        if link in trial_dataset_path[0]:
            print(link)
            for num_layers, hidden_size, gap, seq_num in best_models_index:
                for model_name in os.listdir(f'{main_path}/dataset/{folder_name}/'):                   
                    if f'hiddenSize{hidden_size}_seq_num{seq_num}_gap{gap}' in model_name:
                        if model_name not in file_predictions:
                            file_predictions[model_name] = {'y_pred': [], 'y_true': []}
                        # Load and evaluate model
                        model = cnnLSTM(num_features_joints=seq_num, num_layers=num_layers, hidden_size=hidden_size, dropout=0.7, bidirectional=True)
                        model.to(device)
                        model.load_state_dict(torch.load(f'{main_path}/dataset/{folder_name}/{model_name}'))
                        model.eval()
                        data = LoadSeqDataset(
                            file_path=trial_dataset_path[0], label=label[0],
                            selected_features=selected_features, seq_num=seq_num, gap=1
                        )
                        #data.sequences = data.sequences[len(data)//2:-1]
                        data.sequences = data.sequences[(len(data)-len(data)//2):-1]
 
                        test_loader = DataLoader(data, batch_size=len(data), shuffle=False)
                        # Run inference
                        df= pd.DataFrame()
                        for batch_idx, (seqs, labels) in enumerate(test_loader):
                            seqs = seqs.float().to(device)
                            with torch.no_grad():
                                predictions = model(seqs)
                                predictions = torch.argmax(predictions, dim=1) + 1
 
                            df['time'] = data.data.time[len(data.data.time)-len(data)-1:-1]
                            df['label'] = labels.cpu().numpy()
                            df['model_out'] = predictions.cpu().detach().numpy()
                            df.model_out[df.label == 0] = 0
                            df['majority_voting'] = majority_voting_last_n(df['model_out'], n)
                            
                        #df.iplot(x='time', y=['model_out', 'majority_voting', 'label'], colors=[ 'lightblue', 'darkblue', 'red'], title='Link ' + str(labels.max().item()))
                        # Collect predictions for current model
                        y_true_filtered = df.label[(df.label != 0) & (df.majority_voting != 0)].tolist()
                        y_pred_filtered = df.majority_voting[(df.label != 0) & (df.majority_voting != 0)].tolist()
                        file_predictions[model_name]['y_pred'].extend(y_pred_filtered)
                        file_predictions[model_name]['y_true'].extend(y_true_filtered)
                        break  # Process only first trial per link
                    
            break
 
for model_name in file_predictions.keys():
    y_pred = file_predictions[model_name]['y_pred']
    y_true = file_predictions[model_name]['y_true']
    matrix = confusion_matrix(y_pred=y_pred, y_true=y_true)
 
    total_samples = sum(sum(row) for row in matrix)
    logging.info(f'{model_name}, total samples: {total_samples}')
    #logging.info(f'\n {matrix}')
    true_positives = sum(matrix[i][i] for i in range(len(matrix)))
 
    overall_accuracy = (true_positives / total_samples) * 100
    failure_rate = [(sum(matrix[i]) - matrix[i][i]) / sum(matrix[i]) * 100 for i in range(len(matrix))]
    logging.info(f'acuracy= {overall_accuracy}, detection failure (links): {failure_rate}')
 